In [1]:
import numpy as np
from plotly.subplots import make_subplots
import sys
import pandas as pd

sys.path.append('..')

from models import LogisticClassifier#type:ignore

In [2]:
n_samples = 1000
X = [[np.random.rand() +4 ]for i in range(n_samples)] + [[np.random.rand() +4.9] for i in range(n_samples)]
y = [[0]]*n_samples + [[1]]*n_samples
X = np.array(X)
y = np.array(y)

df = pd.DataFrame(data = {'X':X.flatten(),'y':y.flatten()})
df['color'] = df.y.astype('str')
fig1 = df.plot(x = 'X',y='y',backend = 'plotly',kind = 'scatter',color = 'color')
fig1

In [13]:
classifier = LogisticClassifier(X,y)
classifier.fit(learning_rate=10,num_iterations = 20000,tolerance=0.0001,print_every=100,reg_lambda=0)
classifier.show_training_history().show()

df['ypred'] = classifier._ypred

Iteration 1 liklihood: 9.999999975123766e-05
Iteration 101 liklihood: 9.999999975123766e-05
Iteration 201 liklihood: 9.999999949999987e-05
Iteration 301 liklihood: 9.999999949999987e-05
Iteration 401 liklihood: 9.999999949999987e-05
Iteration 501 liklihood: 9.999999949999987e-05
Iteration 601 liklihood: 0.0006486344296467011
Iteration 701 liklihood: 0.002805433618846706
Iteration 801 liklihood: 0.0014454397614228397
Iteration 901 liklihood: 0.005970352822732416
Iteration 1001 liklihood: 0.008790225036514599
Iteration 1101 liklihood: 0.028313919729642027
Iteration 1201 liklihood: 0.03133285698873306
Iteration 1301 liklihood: 0.03564511305069096
Iteration 1401 liklihood: 0.0409260656343234
Iteration 1501 liklihood: 0.04285485168447723
Iteration 1601 liklihood: 0.04613175707176041
Iteration 1701 liklihood: 0.051324054147068754
Iteration 1801 liklihood: 0.054947219316825856
Iteration 1901 liklihood: 0.05754399324746895
Iteration 2001 liklihood: 0.0580764412610949
Iteration 2101 liklihood: 

In [14]:
newdf = pd.DataFrame(data = {'X':np.linspace(0.99*df.X.min(),0.99*df.X.max(),10000)})
newdf['yprob'] = classifier.predict(newdf.X.values,probabilities=True)
newdf['ypred'] = classifier.predict(newdf.X.values,probabilities=False)

fig1 = df.plot(x = 'X',y='y',backend = 'plotly',kind = 'scatter',color = 'color')
fig3 = newdf.plot(x = 'X',y='yprob',backend = 'plotly',kind = 'line')

fig1.add_trace(fig3.data[0])

In [16]:


def separate_circles(n_samples,centre1:np.ndarray,radius1:float,centre2:np.ndarray,radius2:float):
    """
    Demonstrate the logistic classifier on 2D data
    """
    # Create 2D sample data
    circle1 = centre1 + radius1*(np.random.randn(n_samples, 2)-0.5)
    circle2 = centre2 + radius2*(np.random.randn(n_samples, 2)-0.5)

    X = np.concatenate([circle1, circle2])
    y = np.concatenate([np.zeros(n_samples), np.ones(n_samples)])


    df = pd.DataFrame(data = {'X1':X[:,0],'X2':X[:,1],'y':y})
    df['color'] = df.y.astype('str')
    fig = df.plot(x = 'X1',y='X2',backend = 'plotly',kind = 'scatter',color = 'color',height=800,width=800)

    # Fit the classifier with 2D data
    classifier_2d = LogisticClassifier(X, y)
    classifier_2d.fit(learning_rate=0.01, num_iterations=2000, tolerance=0.0001, print_every=None)

    # draw boundary heat map
    newdf = pd.DataFrame(data = {'X1':np.linspace(df.X1.min(),df.X1.max(),100)})
    newdf = pd.merge(newdf,pd.DataFrame(data = {'X2':np.linspace(df.X2.min(),df.X2.max(),100)}),how = 'cross')
    newdf['yprob'] = classifier_2d.predict(newdf[['X1','X2']].values, probabilities=True)
    newdf['ypred'] = classifier_2d.predict(newdf[['X1','X2']].values, probabilities=False)

    fig1 = df.plot(x = 'X1',y='X2',backend = 'plotly',kind = 'scatter',color = 'color',height=800,width=800)
    fig2 = newdf.plot(x = 'X1',y='X2',backend = 'plotly',kind = 'scatter',color='yprob',height=800,width=800,color_continuous_scale='rainbow')
    fig2.update_traces(marker=dict(size=3))
    fig1.add_trace(fig2.data[0])

    # draw boundary line
    """
    b1*x1 + b2*x2 + c = z <- equation of the separation plane
    the boundary is where z = 0.5
    b1*x1 + b2*x2 + c = 0.5
    x2 = (-b1*x1 - c + 0.5)/b2
    """
    b1 = classifier_2d.theta[0]
    b2 = classifier_2d.theta[1]
    c  = classifier_2d.theta[2]

    newdf['X2'] = (-b1*newdf.X1 - c + 0.5)/b2
    fig3 = newdf.plot(x = 'X1',y='X2',backend = 'plotly',kind = 'line',height=800,width=800)
    fig1.add_trace(fig3.data[0])

    # show fig1 and fig side by side
    fig_combined = make_subplots(rows=1, cols=2, subplot_titles=("Original Data", "Decision Boundary"))
    for trace in fig.data:
        fig_combined.add_trace(trace, row=1, col=1)
    for trace in fig1.data:
        fig_combined.add_trace(trace, row=1, col=2)

    fig_combined.update_layout(height=800, width=1600, title_text="Logistic Classifier on 2D Data")
    fig_combined.show()
    # fig.show()
    # fig1.show()

separate_circles(1000, np.array([0, 0]), 1, np.array([2, 2]), 1)


In [17]:
separate_circles(1000, np.array([0, 0]), 1, np.array([5, 5]), 1)

Tolerance reached
